In [1]:
import pandas as pd

df = pd.read_csv('meta.csv')

df

source_file  n_rows  n_cols  \
0    ./train_separated/data_DEEPSEEKforTextClassifi...   17595     678   
1    ./train_separated/data_DEEPSEEKforTextClassifi...   19203     678   
2    ./train_separated/data_DEEPSEEKforTextClassifi...   18854     678   
3    ./train_separated/data_DEEPSEEKforTextClassifi...   17782     678   
4    ./train_separated/data_DEEPSEEKforTextClassifi...   17700     678   
..                                                 ...     ...     ...   
675  ./infer_separated/infer_ViTL16forImageSemantic...      93     678   
676  ./infer_separated/infer_ViTL16forImageSemantic...      94     678   
677  ./infer_separated/infer_ViTL16forImageSemantic...     106     678   
678  ./infer_separated/infer_ViTL16forImageSemantic...     114     678   
679  ./infer_separated/infer_ViTL16forImageSemantic...     105     678   

           phase    mode     model                       task  dataset  \
0    fine-tuning     llm  DEEPSEEK         TextClassification  default   
1    fine-tuning     llm  DEEPSEEK         TextClassification  default   
2    fine-tuning     llm  DEEPSEEK         TextClassification  default   
3    fine-tuning     llm  DEEPSEEK         TextClassification  default   
4    fine-tuning     llm  DEEPSEEK         TextClassification  default   
..           ...     ...       ...                        ...      ...   
675        infer  nonllm    ViTL16  ImageSemanticSegmentation  default   
676        infer  nonllm    ViTL16  ImageSemanticSegmentation  default   
677        infer  nonllm    ViTL16  ImageSemanticSegmentation  default   
678        infer  nonllm    ViTL16  ImageSemanticSegmentation  default   
679        infer  nonllm    ViTL16  ImageSemanticSegmentation  default   

                            model_task  \
0         DEEPSEEK__TextClassification   
1         DEEPSEEK__TextClassification   
2         DEEPSEEK__TextClassification   
3         DEEPSEEK__TextClassification   
4         DEEPSEEK__TextClassification   
..                                 ...   
675  ViTL16__ImageSemanticSegmentation   
676  ViTL16__ImageSemanticSegmentation   
677  ViTL16__ImageSemanticSegmentation   
678  ViTL16__ImageSemanticSegmentation   
679  ViTL16__ImageSemanticSegmentation   

                                       workload  
0         DEEPSEEK__TextClassification__default  
1         DEEPSEEK__TextClassification__default  
2         DEEPSEEK__TextClassification__default  
3         DEEPSEEK__TextClassification__default  
4         DEEPSEEK__TextClassification__default  
..                                          ...  
675  ViTL16__ImageSemanticSegmentation__default  
676  ViTL16__ImageSemanticSegmentation__default  
677  ViTL16__ImageSemanticSegmentation__default  
678  ViTL16__ImageSemanticSegmentation__default  
679  ViTL16__ImageSemanticSegmentation__default  

[680 rows x 10 columns]

In [2]:
import re
import pandas as pd

# ==== Memory-related Metrics Description Text ====
memory_text = """
Perf:Cache_Misses.*[count] — Cache misses (cumulative counter).
Perf:Cache_References.*[count] — Cache reference accesses (cumulative counter).
Perf:Cycle_activity_cycles_l3_miss.*[count] — Cycles lost due to L3 cache misses (cumulative counter).
Perf:Cycle_activity_stalls_l3_miss.*[count] — Stalls caused by L3 misses (cumulative counter).
Perf:Hle_retired_aborted.*[count] — HLE (hardware lock elision) aborted transactions (cumulative counter).
Perf:Hle_retired_commit.*[count] — HLE committed transactions (cumulative counter).
Perf:Mem_trans_retired_load_latency_gt_128.*[count] — Loads with latency >128 cycles (cumulative counter).
Perf:Mem_trans_retired_load_latency_gt_256.*[count] — Loads with latency >256 cycles (cumulative counter).
Perf:Mem-loads.*[count] — Memory load operations (cumulative counter).
Perf:Mem-stores.*[count] — Memory store operations (cumulative counter).
Memory:Active.*[kB] — Amount of active (recently used) memory. (instant)
Memory:AnonHugePages.*[kB] — Anonymous hugepages memory. (instant)
Memory:AnonPages.*[kB] — Anonymous pages (non-file-backed). (instant)
Memory:Bounce.*[kB] — Bounce buffer memory used (DMA-related). (instant)
Memory:Buffers.*[kB] — Kernel buffers. (instant)
Memory:Cached.*[kB] — File pages cached in memory. (instant)
Memory:CommitLimit.*[kB] — Commit limit for virtual memory. (instant)
Memory:Committed_AS.*[kB] — Committed virtual memory. (instant)
Memory:DirectMap1G.*[kB] — 1 GiB direct-mapped pages. (instant)
Memory:DirectMap2M.*[kB] — 2 MiB direct-mapped pages. (instant)
Memory:DirectMap4k.*[kB] — 4 KiB direct-mapped pages. (instant)
Memory:Dirty.*[kB] — Pages waiting to be written to storage. (instant)
Memory:HardwareCorrupted.*[kB] — Memory marked as hardware-corrupted. (instant)
Memory:Hugepagesize.*[kB] — Hugepage size. (instant)
Memory:Hugetlb.*[kB] — hugetlb allocations. (instant)
Memory:Inactive.*[kB] — Inactive page cache. (instant)
Memory:KReclaimable.*[kB] — Kernel reclaimable memory. (instant)
Memory:KernelStack.*[kB] — Kernel stack usage. (instant)
Memory:Mapped.*[kB] — Mapped files/devices. (instant)
Memory:MemAvailable.*[kB] — Estimated available memory. (instant)
Memory:MemFree.*[kB] — Free physical memory. (instant)
Memory:MemTotal.*[kB] — Total physical memory. (instant)
Memory:Mlocked.*[kB] — Memory locked by mlock. (instant)
Memory:NFS_Unstable.*[kB] — NFS unstable writeback memory. (instant)
Memory:PageTables.*[kB] — Memory used by page tables. (instant)
Memory:SReclaimable.*[kB] — Reclaimable slab memory. (instant)
Memory:SUnreclaim.*[kB] — Unreclaimable slab memory. (instant)
Memory:Shmem.*[kB] — Shared memory usage. (instant)
Memory:ShmemHugePages.*[kB] — Shared memory hugepages. (instant)
Memory:ShmemPmdMapped.*[kB] — PMD-mapped shared memory. (instant)
Memory:Slab.*[kB] — Kernel slab usage. (instant)
Memory:SwapCached.*[kB] — Swap cached memory. (instant)
Memory:SwapFree.*[kB] — Free swap space. (instant)
Memory:SwapTotal.*[kB] — Total swap space. (instant)
Memory:Unevictable.*[kB] — Unevictable pages. (instant)
Memory:VmallocChunk.*[kB] — Largest contiguous vmalloc chunk. (instant)
Memory:VmallocTotal.*[kB] — Total vmalloc address space. (instant)
Memory:VmallocUsed.*[kB] — Vmalloc used. (instant)
Memory:Writeback.*[kB] — Currently writing back pages. (instant)
Memory:WritebackTmp.*[kB] — Temporary writeback usage. (instant)
Memory:MemoryUtilization.*[%] — Memory utilization percent (sampled/derived).
"""

# ==== Extract Metrics and Descriptions ====
memory_metrics = re.findall(r"^([A-Za-z0-9_:.*\[\]]+)\s+—\s+(.*)$", memory_text, flags=re.M)
df_metrics = pd.DataFrame(memory_metrics, columns=["metric_pattern", "description"])


In [ ]:
# ==== Only focus on 'llm' mode and 'infer' phase ====
for file in df[(df['mode'] == 'llm') & (df['phase'] == 'infer')]['source_file'].tolist():
    print(f"Reading: {file}")
    data = pd.read_csv(file, sep='\t', header=0)

    # ==== Find matching columns based on the memory patterns ====
    matched_cols = []
    for pattern in df_metrics["metric_pattern"]:
        # Replace .* in the regular expression with the actual regular expression matching pattern
        regex = pattern.replace(".*", ".*")
        matched = [col for col in data.columns if re.match(regex, col)]
        matched_cols.extend(matched)

    # Deduplication and sorting
    matched_cols = list(sorted(set(matched_cols)))

    print(f"Matched {len(matched_cols)} columns:")
    print(matched_cols)

    # ==== Extract data from these columns ====
    data_selected = data[matched_cols]

    # ==== Optional: Merge description information (matching by regular expression pattern) ====
    # Create a mapping for metric_name -> description (using the first matching rule)
    desc_map = {}
    for _, row in df_metrics.iterrows():
        regex = row['metric_pattern'].replace(".*", ".*")
        for col in matched_cols:
            if re.match(regex, col):
                desc_map[col] = row['description']

    desc_df = pd.DataFrame(list(desc_map.items()), columns=["metric_name", "description"])

    # display(desc_df.head())
    display(data_selected.head())

    # break

Reading: ./infer_separated/data_DEEPSEEKforInference_default_2025-04-26T09-41-59_htc-g003.txt
Matched 48 columns:
['Memory:Active.htc-g003[kB]', 'Memory:AnonHugePages.htc-g003[kB]', 'Memory:AnonPages.htc-g003[kB]', 'Memory:Bounce.htc-g003[kB]', 'Memory:Buffers.htc-g003[kB]', 'Memory:Cached.htc-g003[kB]', 'Memory:CommitLimit.htc-g003[kB]', 'Memory:Committed_AS.htc-g003[kB]', 'Memory:DirectMap1G.htc-g003[kB]', 'Memory:DirectMap2M.htc-g003[kB]', 'Memory:DirectMap4k.htc-g003[kB]', 'Memory:Dirty.htc-g003[kB]', 'Memory:HardwareCorrupted.htc-g003[kB]', 'Memory:Hugepagesize.htc-g003[kB]', 'Memory:Hugetlb.htc-g003[kB]', 'Memory:Inactive.htc-g003[kB]', 'Memory:KReclaimable.htc-g003[kB]', 'Memory:KernelStack.htc-g003[kB]', 'Memory:Mapped.htc-g003[kB]', 'Memory:MemAvailable.htc-g003[kB]', 'Memory:MemFree.htc-g003[kB]', 'Memory:MemTotal.htc-g003[kB]', 'Memory:Mlocked.htc-g003[kB]', 'Memory:NFS_Unstable.htc-g003[kB]', 'Memory:PageTables.htc-g003[kB]', 'Memory:SReclaimable.htc-g003[kB]', 'Memory:SUnr

Memory:Active.htc-g003[kB]  Memory:AnonHugePages.htc-g003[kB]  \
0                   3428672.0                          3518464.0   
1                   3430244.0                          3518464.0   
2                   3427704.0                          3530752.0   
3                   3425164.0                          3543040.0   
4                   3433818.0                          3543040.0   

   Memory:AnonPages.htc-g003[kB]  Memory:Bounce.htc-g003[kB]  \
0                      4742182.0                         0.0   
1                      4741612.0                         0.0   
2                      4738266.0                         0.0   
3                      4734920.0                         0.0   
4                      4743488.0                         0.0   

   Memory:Buffers.htc-g003[kB]  Memory:Cached.htc-g003[kB]  \
0                     123142.0                  12095568.0   
1                     126036.0                  12106924.0   
2                     126740.0                  12113848.0   
3                     127444.0                  12120772.0   
4                     127444.0                  12141372.0   

   Memory:CommitLimit.htc-g003[kB]  Memory:Committed_AS.htc-g003[kB]  \
0                      198345664.0                        10524964.0   
1                      198345664.0                        10450676.0   
2                      198345664.0                        10450676.0   
3                      198345664.0                        10450676.0   
4                      198345664.0                        10450676.0   

   Memory:DirectMap1G.htc-g003[kB]  Memory:DirectMap2M.htc-g003[kB]  ...  \
0                      355467264.0                       44957696.0  ...   
1                      355467264.0                       44957696.0  ...   
2                      355467264.0                       44957696.0  ...   
3                      355467264.0                       44957696.0  ...   
4                      355467264.0                       44957696.0  ...   

   Memory:Writeback.htc-g003[kB]  Memory:WritebackTmp.htc-g003[kB]  \
0                            0.0                               0.0   
1                            0.0                               0.0   
2                            0.0                               0.0   
3                            0.0                               0.0   
4                            0.0                               0.0   

   Perf:Cache_Misses.htc-g003[count]  Perf:Cache_References.htc-g003[count]  \
0                           600101.0                              4254592.0   
1                           502324.0                              2698586.0   
2                           809912.0                              6062539.0   
3                           792834.0                              4563420.0   
4                          1261297.0                              7487200.0   

   Perf:Cycle_activity_cycles_l3_miss.htc-g003[count]  \
0                                         38348655.5    
1                                         32410375.0    
2                                         46650477.0    
3                                         42079254.0    
4                                         63299597.0    

   Perf:Cycle_activity_stalls_l3_miss.htc-g003[count]  \
0                                         34343591.0    
1                                         28945101.0    
2                                         42472086.0    
3                                         38866957.0    
4                                         56744584.0    

   Perf:Hle_retired_aborted.htc-g003[count]  \
0                                       0.0   
1                                       0.0   
2                                       0.0   
3                                       0.0   
4                                       0.0   

   Perf:Hle_retired_commit.htc-g003[count]  \
0                                  

Reading: ./infer_separated/data_DEEPSEEKforInference_default_2025-04-26T17-25-16_htc-g003.txt
Matched 48 columns:
['Memory:Active.htc-g003[kB]', 'Memory:AnonHugePages.htc-g003[kB]', 'Memory:AnonPages.htc-g003[kB]', 'Memory:Bounce.htc-g003[kB]', 'Memory:Buffers.htc-g003[kB]', 'Memory:Cached.htc-g003[kB]', 'Memory:CommitLimit.htc-g003[kB]', 'Memory:Committed_AS.htc-g003[kB]', 'Memory:DirectMap1G.htc-g003[kB]', 'Memory:DirectMap2M.htc-g003[kB]', 'Memory:DirectMap4k.htc-g003[kB]', 'Memory:Dirty.htc-g003[kB]', 'Memory:HardwareCorrupted.htc-g003[kB]', 'Memory:Hugepagesize.htc-g003[kB]', 'Memory:Hugetlb.htc-g003[kB]', 'Memory:Inactive.htc-g003[kB]', 'Memory:KReclaimable.htc-g003[kB]', 'Memory:KernelStack.htc-g003[kB]', 'Memory:Mapped.htc-g003[kB]', 'Memory:MemAvailable.htc-g003[kB]', 'Memory:MemFree.htc-g003[kB]', 'Memory:MemTotal.htc-g003[kB]', 'Memory:Mlocked.htc-g003[kB]', 'Memory:NFS_Unstable.htc-g003[kB]', 'Memory:PageTables.htc-g003[kB]', 'Memory:SReclaimable.htc-g003[kB]', 'Memory:SUnr

Memory:Active.htc-g003[kB]  Memory:AnonHugePages.htc-g003[kB]  \
0                   3625438.0                          3538944.0   
1                   3632036.0                          3540992.0   
2                   3638634.0                          3543040.0   
3                   3645232.0                          3545088.0   
4                   3645360.0                          3545088.0   

   Memory:AnonPages.htc-g003[kB]  Memory:Bounce.htc-g003[kB]  \
0                      4727752.0                         0.0   
1                      4731000.0                         0.0   
2                      4734248.0                         0.0   
3                      4737496.0                         0.0   
4                      4737034.0                         0.0   

   Memory:Buffers.htc-g003[kB]  Memory:Cached.htc-g003[kB]  \
0                     121032.0                  13018674.0   
1                     123028.0                  13023272.0   
2                     125024.0                  13027870.0   
3                     127020.0                  13032468.0   
4                     127232.0                  13041036.0   

   Memory:CommitLimit.htc-g003[kB]  Memory:Committed_AS.htc-g003[kB]  \
0                      198345664.0                        10479140.0   
1                      198345664.0                        10510484.0   
2                      198345664.0                        10541828.0   
3                      198345664.0                        10573172.0   
4                      198345664.0                        10573172.0   

   Memory:DirectMap1G.htc-g003[kB]  Memory:DirectMap2M.htc-g003[kB]  ...  \
0                      355467264.0                       44955648.0  ...   
1                      355467264.0                       44955648.0  ...   
2                      355467264.0                       44955648.0  ...   
3                      355467264.0                       44955648.0  ...   
4                      355467264.0                       44955648.0  ...   

   Memory:Writeback.htc-g003[kB]  Memory:WritebackTmp.htc-g003[kB]  \
0                            0.0                               0.0   
1                            0.0                               0.0   
2                            0.0                               0.0   
3                            0.0                               0.0   
4                            0.0                               0.0   

   Perf:Cache_Misses.htc-g003[count]  Perf:Cache_References.htc-g003[count]  \
0                           685369.0                              4505154.0   
1                           669139.0                              4095071.0   
2                           582753.0                              4181388.0   
3                           485708.0                              4250065.0   
4                           956000.0                              3976584.0   

   Perf:Cycle_activity_cycles_l3_miss.htc-g003[count]  \
0                                         35119997.0    
1                                         30670049.0    
2                                         31822560.0    
3                                         27048502.0    
4                                         40991701.0    

   Perf:Cycle_activity_stalls_l3_miss.htc-g003[count]  \
0                                         31882568.0    
1                                         28317866.0    
2                                         30059964.0    
3                                         21706561.0    
4                                         36074468.0    

   Perf:Hle_retired_aborted.htc-g003[count]  \
0                                       0.0   
1                                       0.0   
2                                       0.0   
3                                       0.0   
4                                       0.0   

   Perf:Hle_retired_commit.htc-g003[count]  \
0                                  

Reading: ./infer_separated/data_DEEPSEEKforInference_default_2025-04-27T01-02-52_htc-g003.txt
Matched 48 columns:
['Memory:Active.htc-g003[kB]', 'Memory:AnonHugePages.htc-g003[kB]', 'Memory:AnonPages.htc-g003[kB]', 'Memory:Bounce.htc-g003[kB]', 'Memory:Buffers.htc-g003[kB]', 'Memory:Cached.htc-g003[kB]', 'Memory:CommitLimit.htc-g003[kB]', 'Memory:Committed_AS.htc-g003[kB]', 'Memory:DirectMap1G.htc-g003[kB]', 'Memory:DirectMap2M.htc-g003[kB]', 'Memory:DirectMap4k.htc-g003[kB]', 'Memory:Dirty.htc-g003[kB]', 'Memory:HardwareCorrupted.htc-g003[kB]', 'Memory:Hugepagesize.htc-g003[kB]', 'Memory:Hugetlb.htc-g003[kB]', 'Memory:Inactive.htc-g003[kB]', 'Memory:KReclaimable.htc-g003[kB]', 'Memory:KernelStack.htc-g003[kB]', 'Memory:Mapped.htc-g003[kB]', 'Memory:MemAvailable.htc-g003[kB]', 'Memory:MemFree.htc-g003[kB]', 'Memory:MemTotal.htc-g003[kB]', 'Memory:Mlocked.htc-g003[kB]', 'Memory:NFS_Unstable.htc-g003[kB]', 'Memory:PageTables.htc-g003[kB]', 'Memory:SReclaimable.htc-g003[kB]', 'Memory:SUnr

...

Memory:Active.htc-g003[kB]  Memory:AnonHugePages.htc-g003[kB]  \
0                3.654930e+06                          3532800.0   
1                3.669184e+06                          3536896.0   
2                3.672308e+06                          3544064.0   
3                3.675432e+06                          3551232.0   
4                3.671791e+06                          3551232.0   

   Memory:AnonPages.htc-g003[kB]  Memory:Bounce.htc-g003[kB]  \
0                   4.733240e+06                         0.0   
1                   4.745072e+06                         0.0   
2                   4.747528e+06                         0.0   
3                   4.749984e+06                         0.0   
4                   4.745833e+06                         0.0   

   Memory:Buffers.htc-g003[kB]  Memory:Cached.htc-g003[kB]  \
0                     124364.0                1.740222e+07   
1                     127444.0                1.740754e+07   
2                     127444.0                1.743627e+07   
3                     127444.0                1.746500e+07   
4                     128012.0                1.747100e+07   

   Memory:CommitLimit.htc-g003[kB]  Memory:Committed_AS.htc-g003[kB]  \
0                      198345664.0                      1.052310e+07   
1                      198345664.0                      1.052310e+07   
2                      198345664.0                      1.053970e+07   
3                      198345664.0                      1.055630e+07   
4                      198345664.0                      1.057001e+07   

   Memory:DirectMap1G.htc-g003[kB]  Memory:DirectMap2M.htc-g003[kB]  ...  \
0                      349175808.0                       51224576.0  ...   
1                      349175808.0                       51224576.0  ...   
2                      349175808.0                       51224576.0  ...   
3                      349175808.0                       51224576.0  ...   
4                      349175808.0                       51224576.0  ...   

   Memory:Writeback.htc-g003[kB]  Memory:WritebackTmp.htc-g003[kB]  \
0                            0.0                               0.0   
1                            0.0                               0.0   
2                            0.0                               0.0   
3                            0.0                               0.0   
4                            0.0                               0.0   

   Perf:Cache_Misses.htc-g003[count]  Perf:Cache_References.htc-g003[count]  \
0                           927359.0                              4978116.0   
1                           861304.0                              5063362.0   
2                          1150372.0                              6280428.0   
3                          1100110.0                              5285265.0   
4                           853844.0                              5238625.0   

   Perf:Cycle_activity_cycles_l3_miss.htc-g003[count]  \
0                                         46976944.0    
1                                         47976585.0    
2                                         71077882.0    
3                                         75444353.0    
4                                         36587137.0    

   Perf:Cycle_activity_stalls_l3_miss.htc-g003[count]  \
0                                         42192429.0    
1                                         43596062.0    
2                                         62338078.0    
3                                         73011698.0    
4                                         32822780.0    

   Perf:Hle_retired_aborted.htc-g003[count]  \
0                                       0.0   
1                                       0.0   
2                                       0.0   
3                                       0.0   
4                                       0.0   

   Perf:Hle_retired_commit.htc-g003[count]  \
0                                  

Reading: ./infer_separated/data_MISTRALforInference_default_2025-04-28T20-43-02_htc-g003.txt
Matched 48 columns:
['Memory:Active.htc-g003[kB]', 'Memory:AnonHugePages.htc-g003[kB]', 'Memory:AnonPages.htc-g003[kB]', 'Memory:Bounce.htc-g003[kB]', 'Memory:Buffers.htc-g003[kB]', 'Memory:Cached.htc-g003[kB]', 'Memory:CommitLimit.htc-g003[kB]', 'Memory:Committed_AS.htc-g003[kB]', 'Memory:DirectMap1G.htc-g003[kB]', 'Memory:DirectMap2M.htc-g003[kB]', 'Memory:DirectMap4k.htc-g003[kB]', 'Memory:Dirty.htc-g003[kB]', 'Memory:HardwareCorrupted.htc-g003[kB]', 'Memory:Hugepagesize.htc-g003[kB]', 'Memory:Hugetlb.htc-g003[kB]', 'Memory:Inactive.htc-g003[kB]', 'Memory:KReclaimable.htc-g003[kB]', 'Memory:KernelStack.htc-g003[kB]', 'Memory:Mapped.htc-g003[kB]', 'Memory:MemAvailable.htc-g003[kB]', 'Memory:MemFree.htc-g003[kB]', 'Memory:MemTotal.htc-g003[kB]', 'Memory:Mlocked.htc-g003[kB]', 'Memory:NFS_Unstable.htc-g003[kB]', 'Memory:PageTables.htc-g003[kB]', 'Memory:SReclaimable.htc-g003[kB]', 'Memory:SUnre

Memory:Active.htc-g003[kB]  Memory:AnonHugePages.htc-g003[kB]  \
0                   3670608.0                          3518464.0   
1                   3675260.0                          3518464.0   
2                   3679912.0                          3518464.0   
3                   3699924.0                          3518464.0   
4                   3691996.0                          3518464.0   

   Memory:AnonPages.htc-g003[kB]  Memory:Bounce.htc-g003[kB]  \
0                   4.748295e+06                         0.0   
1                   4.751981e+06                         0.0   
2                   4.755668e+06                         0.0   
3                   4.775656e+06                         0.0   
4                   4.767982e+06                         0.0   

   Memory:Buffers.htc-g003[kB]  Memory:Cached.htc-g003[kB]  \
0                125921.333333                1.817987e+07   
1                126682.666667                1.818525e+07   
2                127444.000000                1.819063e+07   
3                127444.000000                1.821376e+07   
4                127444.000000                1.822836e+07   

   Memory:CommitLimit.htc-g003[kB]  Memory:Committed_AS.htc-g003[kB]  \
0                      198345664.0                      1.055182e+07   
1                      198345664.0                      1.056261e+07   
2                      198345664.0                      1.057340e+07   
3                      198345664.0                      1.054064e+07   
4                      198345664.0                      1.054064e+07   

   Memory:DirectMap1G.htc-g003[kB]  Memory:DirectMap2M.htc-g003[kB]  ...  \
0                      349175808.0                       51224576.0  ...   
1                      349175808.0                       51224576.0  ...   
2                      349175808.0                       51224576.0  ...   
3                      349175808.0                       51224576.0  ...   
4                      349175808.0                       51224576.0  ...   

   Memory:Writeback.htc-g003[kB]  Memory:WritebackTmp.htc-g003[kB]  \
0                            0.0                               0.0   
1                            0.0                               0.0   
2                            0.0                               0.0   
3                            0.0                               0.0   
4                            0.0                               0.0   

   Perf:Cache_Misses.htc-g003[count]  Perf:Cache_References.htc-g003[count]  \
0                           956801.0                              4497859.0   
1                           870588.0                              6007381.0   
2                           846375.0                              3431604.0   
3                           802675.0                              4980645.0   
4                           540538.0                              4304311.0   

   Perf:Cycle_activity_cycles_l3_miss.htc-g003[count]  \
0                                         40994973.0    
1                                         37080420.0    
2                                         42464765.0    
3                                         49150743.0    
4                                         32710140.0    

   Perf:Cycle_activity_stalls_l3_miss.htc-g003[count]  \
0                                         36723972.0    
1                                         34068992.0    
2                                         41273760.0    
3                                         46447084.0    
4                                         30730095.0    

   Perf:Hle_retired_aborted.htc-g003[count]  \
0                                       0.0   
1                                       0.0   
2                                       0.0   
3                                       0.0   
4                                       0.0   

   Perf:Hle_retired_commit.htc-g003[count]  \
0                                  

Reading: ./infer_separated/data_MISTRALforInference_default_2025-04-29T04-11-47_htc-g003.txt
Matched 48 columns:
['Memory:Active.htc-g003[kB]', 'Memory:AnonHugePages.htc-g003[kB]', 'Memory:AnonPages.htc-g003[kB]', 'Memory:Bounce.htc-g003[kB]', 'Memory:Buffers.htc-g003[kB]', 'Memory:Cached.htc-g003[kB]', 'Memory:CommitLimit.htc-g003[kB]', 'Memory:Committed_AS.htc-g003[kB]', 'Memory:DirectMap1G.htc-g003[kB]', 'Memory:DirectMap2M.htc-g003[kB]', 'Memory:DirectMap4k.htc-g003[kB]', 'Memory:Dirty.htc-g003[kB]', 'Memory:HardwareCorrupted.htc-g003[kB]', 'Memory:Hugepagesize.htc-g003[kB]', 'Memory:Hugetlb.htc-g003[kB]', 'Memory:Inactive.htc-g003[kB]', 'Memory:KReclaimable.htc-g003[kB]', 'Memory:KernelStack.htc-g003[kB]', 'Memory:Mapped.htc-g003[kB]', 'Memory:MemAvailable.htc-g003[kB]', 'Memory:MemFree.htc-g003[kB]', 'Memory:MemTotal.htc-g003[kB]', 'Memory:Mlocked.htc-g003[kB]', 'Memory:NFS_Unstable.htc-g003[kB]', 'Memory:PageTables.htc-g003[kB]', 'Memory:SReclaimable.htc-g003[kB]', 'Memory:SUnre

Memory:Active.htc-g003[kB]  Memory:AnonHugePages.htc-g003[kB]  \
0                3.667975e+06                          3528704.0   
1                3.674965e+06                          3528704.0   
2                3.681956e+06                          3528704.0   
3                3.676670e+06                          3528704.0   
4                3.671384e+06                          3528704.0   

   Memory:AnonPages.htc-g003[kB]  Memory:Bounce.htc-g003[kB]  \
0                   4.738847e+06                         0.0   
1                   4.744241e+06                         0.0   
2                   4.749636e+06                         0.0   
3                   4.744692e+06                         0.0   
4                   4.739748e+06                         0.0   

   Memory:Buffers.htc-g003[kB]  Memory:Cached.htc-g003[kB]  \
0                124237.333333                1.881849e+07   
1                125822.666667                1.882113e+07   
2                127408.000000                1.882378e+07   
3                127426.000000                1.884106e+07   
4                127444.000000                1.885834e+07   

   Memory:CommitLimit.htc-g003[kB]  Memory:Committed_AS.htc-g003[kB]  \
0                      198345664.0                        10516264.0   
1                      198345664.0                        10516264.0   
2                      198345664.0                        10516264.0   
3                      198345664.0                        10516264.0   
4                      198345664.0                        10516264.0   

   Memory:DirectMap1G.htc-g003[kB]  Memory:DirectMap2M.htc-g003[kB]  ...  \
0                      349175808.0                       51224576.0  ...   
1                      349175808.0                       51224576.0  ...   
2                      349175808.0                       51224576.0  ...   
3                      349175808.0                       51224576.0  ...   
4                      349175808.0                       51224576.0  ...   

   Memory:Writeback.htc-g003[kB]  Memory:WritebackTmp.htc-g003[kB]  \
0                            0.0                               0.0   
1                            0.0                               0.0   
2                            0.0                               0.0   
3                            0.0                               0.0   
4                            0.0                               0.0   

   Perf:Cache_Misses.htc-g003[count]  Perf:Cache_References.htc-g003[count]  \
0                           620669.0                              4704444.0   
1                           714584.0                              3781736.0   
2                           668639.0                              5018224.0   
3                           730770.0                              3723095.0   
4                           792811.0                              5666444.0   

   Perf:Cycle_activity_cycles_l3_miss.htc-g003[count]  \
0                                         33430454.0    
1                                         35106802.0    
2                                         34821226.0    
3                                         33492844.0    
4                                         40574790.0    

   Perf:Cycle_activity_stalls_l3_miss.htc-g003[count]  \
0                                         30039258.0    
1                                         33079280.0    
2                                         31553251.0    
3                                         30858957.0    
4                                         35780826.0    

   Perf:Hle_retired_aborted.htc-g003[count]  \
0                                       0.0   
1                                       0.0   
2                                       0.0   
3                                       0.0   
4                                       0.0   

   Perf:Hle_retired_commit.htc-g003[count]  \
0                                  